In [1]:
# Imports and .env setup

import os

import pandas as pd
import plotly.express as px
import supabase
from dotenv import load_dotenv

import psycopg2

load_dotenv()

supabase_client_url = os.getenv("SUPABASE_URL")
supabase_client_key = os.getenv("SUPABASE_KEY")
supabase_client_user = os.getenv("SUPABASE_USER")
supabase_client_password = os.getenv("SUPABASE_USER_PASSWORD")
supabase_postgres_host = os.getenv("SUPABASE_POSTGRES_HOST")
supabase_postgres_user = os.getenv("SUPABASE_POSTGRES_USER")
supabase_postgres_password = os.getenv("SUPABASE_POSTGRES_PASSWORD")

In [2]:
# Setup for Supabase and Postgres connection for SQL queries that are not suported in the supabase client

supabase_client = supabase.create_client(supabase_client_url, supabase_client_key)
supabase_auth = supabase_client.auth.sign_in_with_password(
    {"email": supabase_client_user, "password": supabase_client_password}
)

conn = psycopg2.connect(
    host=supabase_postgres_host,
    user=supabase_postgres_user,
    password=supabase_postgres_password,
    dbname="postgres",
    port="6543",
)

cursor = conn.cursor()

In [3]:
# Load all data from the table "appliances_use"

df_appliances = pd.DataFrame(
    supabase_client.table("appliances_use").select("*").execute().data
).set_index("id")

df_appliances

created_at           type  appliance_external_id  \
id                                                                             
1222  2024-07-12T00:54:47.830873+00:00  Waschmaschine                  47625   
1223  2024-07-12T00:54:55.356663+00:00  Waschmaschine                  47626   
1224  2024-07-12T00:54:56.764142+00:00       Trockner                  47629   
1225  2024-07-12T00:55:07.902867+00:00  Waschmaschine                  47625   
1226  2024-07-12T00:55:08.048464+00:00  Waschmaschine                  47626   
...                                ...            ...                    ...   
7148  2024-08-01T19:30:15.697462+00:00  Waschmaschine                  47626   
7149  2024-08-01T19:30:18.250475+00:00       Trockner                  47629   
7150   2024-08-01T19:30:19.66384+00:00  Waschmaschine                  47625   
7151  2024-08-01T19:30:24.805324+00:00       Trockner                  47629   
7152  2024-08-01T19:30:26.185636+00:00  Waschmaschine                  47627   

     running_for                       file_name             date_collected  
id                                                                           
1222    00:15:07  Screenshot_20240630-013028.png  2024-06-30T01:30:28+00:00  
1223    01:02:03  Screenshot_20240701-141028.png  2024-07-01T14:10:28+00:00  
1224    00:09:14  Screenshot_20240628-211045.png  2024-06-28T21:10:45+00:00  
1225    00:02:59  Screenshot_20240628-193527.png  2024-06-28T19:35:27+00:00  
1226    00:04:02  Screenshot_20240628-193527.png  2024-06-28T19:35:27+00:00  
...          ...                             ...                        ...  
7148    00:06:22  Screenshot_20240720-072529.png  2024-07-20T07:25:29+00:00  
7149    01:59:09  Screenshot_20240722-030539.png  2024-07-22T03:05:39+00:00  
7150    00:01:29  Screenshot_20240725-092529.png  2024-07-25T09:25:29+00:00  
7151    00:54:38  Screenshot_20240726-113040.png  2024-07-26T11:30:40+00:00  
7152    00:00:07  Screenshot_20240726-094027.png  2024-07-26T09:40:27+00:00  

[7134 rows x 6 columns]

In [4]:
# Load all data from the table "time_updates" - this is when the screenshots were taken

df_updated = pd.DataFrame(
    supabase_client.table("time_updates").select("*").execute().data
).set_index("id")

df_updated["update_time"] = pd.to_datetime(df_updated["update_time"], utc=True)

df_updated

created_at               update_time  \
id                                                                  
1237   2024-07-12T00:29:47.593067+00:00 2024-06-28 04:10:28+00:00   
1238   2024-07-12T00:29:48.704148+00:00 2024-07-02 02:45:45+00:00   
1239    2024-07-12T00:29:49.83023+00:00 2024-07-02 02:15:27+00:00   
1240   2024-07-12T00:29:51.277008+00:00 2024-06-30 21:40:27+00:00   
1241     2024-07-12T00:29:52.5535+00:00 2024-07-02 18:40:26+00:00   
...                                 ...                       ...   
15717  2024-08-01T19:30:25.003871+00:00 2024-07-26 11:30:40+00:00   
15718  2024-08-01T19:30:26.374927+00:00 2024-07-26 09:40:27+00:00   
15719  2024-08-01T19:30:27.546031+00:00 2024-07-18 12:35:40+00:00   
15720  2024-08-01T19:30:28.712062+00:00 2024-07-19 20:40:39+00:00   
15721  2024-08-01T19:30:29.917017+00:00 2024-07-25 06:20:41+00:00   

                            file_name  
id                                     
1237   Screenshot_20240628-041028.png  
1238   Screenshot_20240702-024545.png  
1239   Screenshot_20240702-021527.png  
1240   Screenshot_20240630-214027.png  
1241   Screenshot_20240702-184026.png  
...                               ...  
15717  Screenshot_20240726-113040.png  
15718  Screenshot_20240726-094027.png  
15719  Screenshot_20240718-123540.png  
15720  Screenshot_20240719-204039.png  
15721  Screenshot_20240725-062041.png  

[15676 rows x 3 columns]

In [5]:
# Find the first and last day of collection

print(f"First day of collection: {pd.to_datetime(df_appliances["date_collected"].min()).strftime("%Y-%m-%d %H:%M:%S"): >19}")
print(f"Last day of collection: {pd.to_datetime(df_appliances["date_collected"].max()).strftime("%Y-%m-%d %H:%M:%S"): >20}")

First day of collection: 2024-06-27 16:55:55
Last day of collection:  2024-07-31 11:40:27


In [6]:
# Count the number of measurements and days in the database

query_number_of_measuments = """
SELECT COUNT(*) FROM appliances_use
"""

query_number_of_days_of_measuments = """
SELECT
  COUNT(DISTINCT(EXTRACT(DOY FROM date_collected)))
FROM appliances_use
"""

cursor.execute(query_number_of_measuments)
number_of_measurements = cursor.fetchone()[0]

cursor.execute(query_number_of_days_of_measuments)
number_of_days = cursor.fetchone()[0]

print(f"Total number of measurements: {number_of_measurements}")
print(f"Total number of days of measurements: {number_of_days}")

Total number of measurements: 7134
Total number of days of measurements: 34


In [7]:
# This query returns the highest time recorded for each appliance for each run

query_get_max_usage = """
WITH
  cte AS
    (
      SELECT *,
        ROW_NUMBER() OVER (ORDER BY appliance_external_id, date_collected) as rn1,
        LAG(running_for, 1) OVER (ORDER BY appliance_external_id, date_collected) as prev_running_for
      FROM appliances_use
      ORDER BY appliance_external_id, date_collected ASC
    ), 
  cte2 AS
    (
      SELECT *, LEAD(running_for - prev_running_for,1) OVER (ORDER BY rn1) AS dif_running
      FROM cte
    )

SELECT id, type, appliance_external_id, running_for, date_collected FROM cte2 WHERE dif_running < '0:0:0'
"""

# Execute query and save result in dataframe
cursor.execute(query_get_max_usage)
df = pd.DataFrame(cursor.fetchall())

# Rename columns with the same name returned by the query
df.columns = [x[0] for x in cursor.description]

# Add running time in seconds column
df["running_for_seconds"] = df["running_for"].map(
    lambda x: x.hour * 3600 + x.minute * 60 + x.second
)

# Add start time and rename end time
df["start_time"] = df["date_collected"] - pd.to_timedelta(df["running_for_seconds"], unit="s")
df = df.rename(columns={"date_collected": "end_time"})

# Add type to external id
df["appliance_external_id"] = df["type"] + " " + df["appliance_external_id"].astype(str)

# Reorder columns
df = df[
    [
        "id",
        "type",
        "appliance_external_id",
        "running_for",
        "start_time",
        "end_time",
        "running_for_seconds",
    ]
]


df

id           type appliance_external_id running_for  \
0    2312  Waschmaschine   Waschmaschine 47625    01:10:03   
1    2070  Waschmaschine   Waschmaschine 47625    01:02:06   
2     612  Waschmaschine   Waschmaschine 47625    00:56:22   
3    1519  Waschmaschine   Waschmaschine 47625    01:00:12   
4     471  Waschmaschine   Waschmaschine 47625    01:06:29   
..    ...            ...                   ...         ...   
564  6465       Trockner        Trockner 47630    01:10:32   
565  6801       Trockner        Trockner 47630    01:10:17   
566  4136       Trockner        Trockner 47630    02:00:07   
567  4391       Trockner        Trockner 47630    01:51:33   
568  6835       Trockner        Trockner 47630    01:58:57   

                   start_time                  end_time  running_for_seconds  
0   2024-06-27 16:10:17+00:00 2024-06-27 17:20:20+00:00                 4203  
1   2024-06-27 17:53:20+00:00 2024-06-27 18:55:26+00:00                 3726  
2   2024-06-27 19:39:04+00:00 2024-06-27 20:35:26+00:00                 3382  
3   2024-06-28 08:25:16+00:00 2024-06-28 09:25:28+00:00                 3612  
4   2024-06-28 12:53:58+00:00 2024-06-28 14:00:27+00:00                 3989  
..                        ...                       ...                  ...  
564 2024-07-28 17:10:08+00:00 2024-07-28 18:20:40+00:00                 4232  
565 2024-07-28 23:40:23+00:00 2024-07-29 00:50:40+00:00                 4217  
566 2024-07-29 20:15:33+00:00 2024-07-29 22:15:40+00:00                 7207  
567 2024-07-30 09:19:07+00:00 2024-07-30 11:10:40+00:00                 6693  
568 2024-07-30 18:31:42+00:00 2024-07-30 20:30:39+00:00                 7137  

[569 rows x 7 columns]

In [8]:
# Create DF Sum and add running hours column

df_sum = (
    df[["appliance_external_id", "running_for_seconds", "type"]]
    .groupby(["appliance_external_id", "type"])
    .sum()
).reset_index()

df_sum["running_for_hours"] = df_sum["running_for_seconds"] / 3600

df_sum

appliance_external_id           type  running_for_seconds  running_for_hours
0        Trockner 47629       Trockner               508480         141.244444
1        Trockner 47630       Trockner               155071          43.075278
2   Waschmaschine 47625  Waschmaschine               442442         122.900556
3   Waschmaschine 47626  Waschmaschine               429859         119.405278
4   Waschmaschine 47627  Waschmaschine               328668          91.296667
5   Waschmaschine 47628  Waschmaschine               302044          83.901111

In [9]:
# Get total number of usage per appliance and add to DF

print("Total number of usage per appliance:")

df_total_usage = (
    df[["appliance_external_id", "type", "id"]]
    .groupby(["appliance_external_id", "type"])
    .count()
    .rename({"id": "number_of_uses"}, axis=1)
    .reset_index()
)

df_sum = df_sum.merge(df_total_usage, on=["appliance_external_id", "type"])

df_sum

Total number of usage per appliance:


appliance_external_id           type  running_for_seconds  \
0        Trockner 47629       Trockner               508480   
1        Trockner 47630       Trockner               155071   
2   Waschmaschine 47625  Waschmaschine               442442   
3   Waschmaschine 47626  Waschmaschine               429859   
4   Waschmaschine 47627  Waschmaschine               328668   
5   Waschmaschine 47628  Waschmaschine               302044   

   running_for_hours  number_of_uses  
0         141.244444              88  
1          43.075278              26  
2         122.900556             131  
3         119.405278             135  
4          91.296667             101  
5          83.901111              88

# Machine properties and cost 

## Washing machine:
- Model: Miele PWM 508
- Energy consumption: 0.472 kWh (ECO Modus)
- Water consumption: 47 Liter / Waschen (ECO Modus)
- Cost per usage: 3.50 eur

## Dryer:
- Model: Miele PT 7135 C
- Energy consumption: 3.68 kWh
- Cost per usage: 2.50 eur


Source:
- https://media.miele.com/downloads/d3/aa/05_F61547C6F7151EDDB0DDE0F735F1D3AA.pdf
- https://cdn.billiger.com/dynimg/ZVgoap4w6fuNGJiOdVYfQft4H9rycHjeBa9LTdXG2DAN70u0YrvbtAqE9IvN5ytIQL-sec3q_mXYdEe_GD27jY/Miele-PT-7135-C-Lotosweiss-Technische-Details-534c2b.pdf

# Average energy price for the region

- 41.75 ct/kWh

Source:
- https://www.destatis.de/DE/Themen/Wirtschaft/Preise/Erdgas-Strom-DurchschnittsPreise/_inhalt.html

# Average water price for the region

- 1.81 € / m3

Source:
- https://www.verivox.de/strom-gas/ratgeber/wasserkosten-berechnen-und-sparen-1000796/

In [10]:
# Add the data above to variables

washing_machine_energy_consumption_kwh = 0.472
washing_machine_water_consumption_liter = 47
price_per_wash = 3.5
drier_energy_consumption_kwh = 3.68
energy_price_kwh = 0.4175
water_price_liter = 1.81 / 1000
price_per_dry = 2.5

In [11]:
# Calculate total cost and revenue

df_sum["energy_consumption_kwh"] = df_sum["running_for_hours"] * (
    (df_sum["type"] == "Waschmaschine") * washing_machine_energy_consumption_kwh
    + (df_sum["type"] == "Trockner") * drier_energy_consumption_kwh
)

df_sum["water_consumption_liter"] = df_sum["running_for_hours"] * (
    (df_sum["type"] == "Waschmaschine") * washing_machine_water_consumption_liter
)


df_sum["total_cost"] = (
    df_sum["energy_consumption_kwh"] * energy_price_kwh
    + df_sum["water_consumption_liter"] * water_price_liter
)

df_sum["revenue"] = (df_sum["type"] == "Waschmaschine") * price_per_wash * df_sum[
    "number_of_uses"
] + (df_sum["type"] == "Trockner") * price_per_dry * df_sum["number_of_uses"]

df_sum["profit"] = df_sum["revenue"] - df_sum["total_cost"]

df_sum

appliance_external_id           type  running_for_seconds  \
0        Trockner 47629       Trockner               508480   
1        Trockner 47630       Trockner               155071   
2   Waschmaschine 47625  Waschmaschine               442442   
3   Waschmaschine 47626  Waschmaschine               429859   
4   Waschmaschine 47627  Waschmaschine               328668   
5   Waschmaschine 47628  Waschmaschine               302044   

   running_for_hours  number_of_uses  energy_consumption_kwh  \
0         141.244444              88              519.779556   
1          43.075278              26              158.517022   
2         122.900556             131               58.009062   
3         119.405278             135               56.359291   
4          91.296667             101               43.092027   
5          83.901111              88               39.601324   

   water_consumption_liter  total_cost  revenue      profit  
0                 0.000000  217.007964    220.0    2.992036  
1                 0.000000   66.180857     65.0   -1.180857  
2              5776.326111   34.673934    458.5  423.826066  
3              5612.048056   33.687811    472.5  438.812189  
4              4290.943333   25.757529    353.5  327.742471  
5              3943.352222   23.671020    308.0  284.328980

In [12]:
# Cumulative sums

df_sum = df_sum.groupby("type").sum()

df_sum.loc["total"] = df_sum.sum()

df_sum

appliance_external_id  \
type                                                               
Trockner                            Trockner 47629Trockner 47630   
Waschmaschine  Waschmaschine 47625Waschmaschine 47626Waschmas...   
total          Trockner 47629Trockner 47630Waschmaschine 4762...   

               running_for_seconds  running_for_hours  number_of_uses  \
type                                                                    
Trockner                    663551         184.319722             114   
Waschmaschine              1503013         417.503611             455   
total                      2166564         601.823333             569   

               energy_consumption_kwh  water_consumption_liter  total_cost  \
type                                                                         
Trockner                   678.296578                 0.000000  283.188821   
Waschmaschine              197.061704             19622.669722  117.790294   
total                      875.358282             19622.669722  400.979115   

               revenue       profit  
type                                 
Trockner         285.0     1.811179  
Waschmaschine   1592.5  1474.709706  
total           1877.5  1476.520885

In [13]:
# Profit per day

print(f"Total Profit per day { df_sum.loc["total", "profit"] / number_of_days:.2f}€")

Total Profit per day 43.43€


# Appliances usage pattern

In [14]:
# Columnws for the creation of the timeline graph with Plotly Express

df_updated.loc[:, "Updated"] = "Data Collection"
df_updated.loc[:, "color"] = "Data Collection"
df_updated.loc[:, "end_update_time"] = df_updated["update_time"] + pd.Timedelta(minutes=5)
df.loc[:, "color"] = "In use"

df_updated.rename(
    columns={
        "update_time": "start_time",
        "end_update_time": "end_time",
        "Updated": "appliance_external_id",
    },
    inplace=True,
)

# Set colors
discrete_map = {
    "Data Collection": "#ff8800",
    "In use": "#0b5394",
}

In [37]:
# Create main graph with the machine usage

fig = px.timeline(
    df[["start_time", "end_time", "appliance_external_id", "color"]],
    x_start="start_time",
    x_end="end_time",
    y="appliance_external_id",
    title="Appliances usage for the period 2024-06-27 - 2024-07-31",
    color="color",
    color_discrete_map=discrete_map,
)

# Create figure with uptime of the system, ie, when the screenshot was correctly made
updated_times_fig = px.timeline(
    df_updated.loc[
        (df_updated["start_time"] >= pd.to_datetime("2024-06-27", utc=True))
        & (df_updated["start_time"] < pd.to_datetime("2024-07-31", utc=True)),
    ],
    x_start="start_time",
    x_end="end_time",
    y="appliance_external_id",
    title="Updated Appliances usage for the period 2024-07-01 - 2024-07-31",
    color="color",
    color_discrete_map=discrete_map,
)

# Remove outline of updated times
updated_times_fig.data[0].marker.line.width = 0

# Add updated times to the figure
fig.add_trace(
    updated_times_fig.data[0],
)

fig.update_layout(yaxis_title="Appliance external ID")
# Y axis is in descending order by default
fig.update_yaxes(autorange="reversed")
# fig.update_layout(showlegend=False)

fig.update_yaxes()

fig.write_image("doc/plots/usage_timeline_and_uptime.png", width=1200, height=500)

fig.show()

### It's hard to read, so we'll split it per week

In [38]:
week = [
    "2024-07-01",
    "2024-07-08",
    "2024-07-15",
    "2024-07-22",
    "2024-07-29",
]

start_week = None
for end_week in week:
    if not start_week:
        start_week = end_week
        continue

    fig = px.timeline(
        df[(df["end_time"] >= start_week) & (df["end_time"] < end_week)],
        x_start="start_time",
        x_end="end_time",
        y="appliance_external_id",
        title="Usage during " + start_week + " - " + end_week,
        color="color",
        color_discrete_map=discrete_map,
    )

    figure_updated_times = px.timeline(
        df_updated.loc[
            (df_updated["start_time"] >= pd.to_datetime(start_week, utc=True))
            & (df_updated["start_time"] < pd.to_datetime(end_week, utc=True)),
        ],
        x_start="start_time",
        x_end="end_time",
        y="appliance_external_id",
        color="color",
        color_discrete_map=discrete_map,
    )

    figure_updated_times.data[0].marker.line.width = 0

    fig.add_trace(
        figure_updated_times.data[0],
    )

    fig.update_layout(yaxis_title="Appliance external ID")
    fig.update_yaxes(autorange="reversed")

    fig.write_image(
        "doc/plots/usage_timeline_and_uptime_" + start_week + "_" + end_week + ".png",
        width=1200,
        height=500,
    )

    fig.show()

    start_week = end_week

## Usage patterns

For this analysis, we'll only consider the wash machines.

In [19]:
# Add minutes pased since start of the day

df.loc[:, "minutes_in_day_start_time"] = df["start_time"].dt.hour * 60 + df["start_time"].dt.minute
df.loc[:, "minutes_in_day_end_time"] = (
    df["minutes_in_day_start_time"] + df["running_for_seconds"] / 60
)

df_updated.loc[:, "minutes_in_day_start_time"] = (
    df_updated["start_time"].dt.hour * 60 + df_updated["start_time"].dt.minute
)
df_updated.loc[:, "minutes_in_day_end_time"] = df_updated["minutes_in_day_start_time"] + 5

df_updated.head(5)

created_at                start_time  \
id                                                                 
1237  2024-07-12T00:29:47.593067+00:00 2024-06-28 04:10:28+00:00   
1238  2024-07-12T00:29:48.704148+00:00 2024-07-02 02:45:45+00:00   
1239   2024-07-12T00:29:49.83023+00:00 2024-07-02 02:15:27+00:00   
1240  2024-07-12T00:29:51.277008+00:00 2024-06-30 21:40:27+00:00   
1241    2024-07-12T00:29:52.5535+00:00 2024-07-02 18:40:26+00:00   

                           file_name appliance_external_id   color  \
id                                                                   
1237  Screenshot_20240628-041028.png               Updated  Uptime   
1238  Screenshot_20240702-024545.png               Updated  Uptime   
1239  Screenshot_20240702-021527.png               Updated  Uptime   
1240  Screenshot_20240630-214027.png               Updated  Uptime   
1241  Screenshot_20240702-184026.png               Updated  Uptime   

                      end_time  minutes_in_day_start_time  \
id                                                          
1237 2024-06-28 04:15:28+00:00                        250   
1238 2024-07-02 02:50:45+00:00                        165   
1239 2024-07-02 02:20:27+00:00                        135   
1240 2024-06-30 21:45:27+00:00                       1300   
1241 2024-07-02 18:45:26+00:00                       1120   

      minutes_in_day_end_time  
id                             
1237                      255  
1238                      170  
1239                      140  
1240                     1305  
1241                     1125

In [20]:
# Create new dataframe with date and time columns and how many appliances are in use
array_use_wash_machine = []

for day in df["start_time"].dt.day_of_year.unique():
    for minute in range(0, 60 * 24, 10):
        # Only add data when the system was in uptime
        if len(
            df_updated[
                (df_updated["start_time"].dt.day_of_year == day)
                & (df_updated["minutes_in_day_start_time"] < minute)
                & (df_updated["minutes_in_day_end_time"] >= minute)
            ]
        ):
            array_use_wash_machine.append(
                [
                    day,  # Day of year
                    pd.Timestamp(minute, unit="m"),  # Time of day
                    len(
                        df[
                            (df["minutes_in_day_start_time"] <= minute)
                            & (df["minutes_in_day_end_time"] > minute)
                            & (df["type"] == "Waschmaschine")
                            & (df["start_time"].dt.day_of_year == day)
                        ]
                    ),
                    day % 7,  # Only works because 2024 starts on Monday
                ]
            )


df_total_usage_per_time = pd.DataFrame(array_use_wash_machine).rename(
    columns={0: "day", 1: "time_of_day", 2: "number_of_appliances_in_use", 3: "weekday"}
)

df_total_usage_per_time

day         time_of_day  number_of_appliances_in_use  weekday
0     179 1970-01-01 17:00:00                            2        4
1     179 1970-01-01 17:10:00                            2        4
2     179 1970-01-01 17:20:00                            2        4
3     179 1970-01-01 17:30:00                            0        4
4     179 1970-01-01 17:40:00                            1        4
...   ...                 ...                          ...      ...
3886  200 1970-01-01 21:40:00                            0        4
3887  200 1970-01-01 21:50:00                            0        4
3888  200 1970-01-01 22:00:00                            0        4
3889  200 1970-01-01 22:10:00                            1        4
3890  200 1970-01-01 22:20:00                            0        4

[3891 rows x 4 columns]

In [21]:
# Create DF with aggregate data per time and weekday

df_aggregation_per_weekday_time = (
    df_total_usage_per_time.loc[:, ["weekday", "time_of_day", "number_of_appliances_in_use"]]
    .groupby(["weekday", "time_of_day"])
    .agg(["min", "mean", "max"])
    .reset_index()
)

# Rename days of the week
dict_weekday = {
    0: "Sunday",
    1: "Monday",
    2: "Tuesday",
    3: "Wednesday",
    4: "Thursday",
    5: "Friday",
    6: "Saturday",
}

df_aggregation_per_weekday_time["weekday"] = df_aggregation_per_weekday_time["weekday"].map(
    dict_weekday
)

# Rename columns
df_aggregation_per_weekday_time.columns = [
    "_".join(col).strip() for col in df_aggregation_per_weekday_time.columns.values
]

# Format time
format_mapping_minute = {"time_of_day": "{:%H:%M}"}

df_aggregation_per_weekday_time

weekday_        time_of_day_  number_of_appliances_in_use_min  \
0       Sunday 1970-01-01 00:10:00                                0   
1       Sunday 1970-01-01 00:20:00                                0   
2       Sunday 1970-01-01 00:30:00                                0   
3       Sunday 1970-01-01 00:40:00                                0   
4       Sunday 1970-01-01 00:50:00                                0   
...        ...                 ...                              ...   
996   Saturday 1970-01-01 23:10:00                                0   
997   Saturday 1970-01-01 23:20:00                                0   
998   Saturday 1970-01-01 23:30:00                                0   
999   Saturday 1970-01-01 23:40:00                                0   
1000  Saturday 1970-01-01 23:50:00                                0   

      number_of_appliances_in_use_mean  number_of_appliances_in_use_max  
0                             0.000000                                0  
1                             0.000000                                0  
2                             0.000000                                0  
3                             0.000000                                0  
4                             0.000000                                0  
...                                ...                              ...  
996                           0.333333                                1  
997                           0.333333                                1  
998                           0.333333                                1  
999                           0.333333                                1  
1000                          0.333333                                1  

[1001 rows x 5 columns]

In [22]:
# Create dataframe with mean usage per weekday

df_most_used_weekday = (
    df_total_usage_per_time.loc[:, ["weekday", "number_of_appliances_in_use"]]
    .groupby("weekday")
    .mean()
    .rename(dict_weekday)
    .reset_index()
    .rename(columns={"number_of_appliances_in_use": "mean_number_of_appliances_in_use"})
)

df_most_used_weekday.sort_values(by="mean_number_of_appliances_in_use", ascending=False)

weekday  mean_number_of_appliances_in_use
5     Friday                          0.838150
0     Sunday                          0.823643
1     Monday                          0.702277
6   Saturday                          0.583658
2    Tuesday                          0.497537
4   Thursday                          0.451786
3  Wednesday                          0.438538

In [31]:
# Create dataframe with aggregate usage pert time

df_most_used_time = (
    df_total_usage_per_time.loc[:, ["time_of_day", "number_of_appliances_in_use"]]
    .groupby("time_of_day")
    .agg(["min", "mean", "max"])
)

# Rename columns
df_most_used_time.columns = [
    "Min number of appliances in use",
    "Mean number of appliances in use",
    "Max number of appliances in use",
]

df_most_used_time.reset_index()

time_of_day  Min number of appliances in use  \
0   1970-01-01 00:10:00                                0   
1   1970-01-01 00:20:00                                0   
2   1970-01-01 00:30:00                                0   
3   1970-01-01 00:40:00                                0   
4   1970-01-01 00:50:00                                0   
..                  ...                              ...   
138 1970-01-01 23:10:00                                0   
139 1970-01-01 23:20:00                                0   
140 1970-01-01 23:30:00                                0   
141 1970-01-01 23:40:00                                0   
142 1970-01-01 23:50:00                                0   

     Mean number of appliances in use  Max number of appliances in use  
0                            0.041667                                1  
1                            0.040000                                1  
2                            0.153846                                1  
3                            0.269231                                3  
4                            0.250000                                2  
..                                ...                              ...  
138                          0.423077                                2  
139                          0.440000                                2  
140                          0.346154                                1  
141                          0.280000                                1  
142                          0.217391                                1  

[143 rows x 4 columns]

In [41]:
# Plot for average use per time of day
fig_average_use = px.line(
    df_aggregation_per_weekday_time,
    x="time_of_day_",
    y="number_of_appliances_in_use_mean",
    color="weekday_",
    title="Average usage per time of day per weekday",
    labels={
        "time_of_day_": "Time of day",
        "number_of_appliances_in_use_mean": "Average number of appliances in use",
    },
)

# Plot for most used weekdays
fig_most_used_weekdays = px.bar(
    df_most_used_weekday,
    x="weekday",
    y="mean_number_of_appliances_in_use",
    title="Most used weekday",
    category_orders={
        "weekday": [
            "Monday",
            "Tuesday",
            "Wednesday",
            "Thursday",
            "Friday",
            "Saturday",
            "Sunday",
        ]
    },
    labels={
        "weekday": "Weekday",
        "mean_number_of_appliances_in_use": "Mean number of appliances in use at any given time",
    },
)

# Plot for most used times
fig_most_used_time = px.line(
    df_most_used_time,
    x=df_most_used_time.index,
    y=df_most_used_time.columns[1:],
    title="Most used times",
    labels={
        "x": "Time of day",
        "y": "Number of appliances in use",
        "variable": "Measument",
        "time_of_day": "Time of day",
    },
)

# Save plots as image
fig_average_use.write_image("doc/plots/average_use_per_time.png", width=1200, height=500)
fig_most_used_weekdays.write_image("doc/plots/most_used_weekdays.png", width=1200, height=500)
fig_most_used_time.write_image("doc/plots/most_used_time.png", width=1200, height=500)

# Show plots
fig_average_use.show()
fig_most_used_weekdays.show()
fig_most_used_time.show()

### Notes

1. The dryer 47630 was defective from 01.07.2024 to 22.07.2024.

# Conclusions

1. The dryers are not profitable and are just breaking even (See limitations #1 below)
2. Friday is the day with most use (average of 0.84 Washing Machines running at any given time) followed closed by Sunday (0.82).
3. The most used time, averaging at least 1 Washing machine running is between 10:50 and 16:00 and from 19:00 to 21:00.
4. The machines are regularly used in the middle of the night all the way till 3am, the earliest anyone has used the machines was around 4:20am.
5. The position of the machines directly corresponds to the number of hours in use, the closest to the door being the most used and so on.
6. The running profit is around 43,43 € per day (1476.52 / 34).


# Limitations

1. The dryer energy consumption was taken directly from the datasheet for the product and is the peak consumption, the average consumption should be lower but since it is an older model an average consumption was not provided as the newer ones.
2. The previous point means the total cost is actually lower.
3. As this project was running on a local Android Machine there were downtime when this machine was needed for another tasks, this is represented in the graphs.
4. As the collectio of data run every 5 minutes, the run time of every machine should be slightly higher, as much as 4:59min per run.
